<a href="https://colab.research.google.com/github/Viplove12/Credit-Card-Fraud-Detection/blob/master/RNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt


In [0]:

dataset=pd.read_csv('/content/drive/My Drive/sentiment analysis/train.csv',encoding='latin-1')

In [7]:
len(dataset)

99989

In [8]:

import re
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
corpus=[]
print("done")

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
done


## **Data PreProcessing**

In [9]:
for i in range(0,len(dataset)):
    review=re.sub('[^a-zA-Z]',' ',dataset['SentimentText'][i])
    review=review.lower()
    review=review.split()
    ps=PorterStemmer()
    review=[ps.stem(word) for word in review if not word in set(stopwords.words('english'))]
    review=' '.join(review)
    corpus.append(review)

all_text=' '.join(corpus)

words=all_text.split()
print('done')

done


In [41]:
all_text

'sad apl friend miss new moon trailer omg alreadi omgaga im sooo im gunna cri dentist sinc supos get crown put min think mi bf cheat worri much juuuuuuuuuuuuuuuuussssst chillin sunni work tomorrow tv tonight hand uniform today miss alreadi hmmmm wonder number must think posit thank hater face day weekend suck far jb isnt show australia ok that win lt way feel right awhh man complet useless rt funni twitter http myloc hx feel strang fine gonna go listen semison celebr huge roll thunder scari cut beard grow well year gonna start shaunamanu happi meantim sad iran wompppp wompp one see caus one els follow pretti awesom lt sad level write massiv blog tweet myspac comp shut lost lay fetal posit head hospitol pull golf tourni rd place think rip someth yeah bore what wrong pleas tell bother wish could spend rest life sat go gig serious feeel like shit right realli want sleep nooo hour danc art assign finish goodby exam hello alcohol tonight realiz deep geez give girl warn atleast hate athlet a

## Encoding (because pytorch take encoded values only)

In [11]:
from collections import Counter
counts=Counter(words)
vocab=sorted(counts,key=counts.get, reverse=True)
vocab_to_int = {word: ii for ii, word in enumerate(vocab, 1)}
reviews_ints = []
for review in corpus:
    reviews_ints.append([vocab_to_int[word] for word in review.split()])
print('done')

done


In [45]:
len(counts)


85033

## Removing 0 lenght tweets

In [13]:


    
review_lens = Counter([len(x) for x in reviews_ints])
print("Zero-length reviews: {}".format(review_lens[0]))
print("Maximum review length: {}".format(max(review_lens)))
sum=0;

#FOR SEQUENCE LENGTH
for x in reviews_ints:
    sum+=len(x);

sum=sum/len(reviews_ints)   

#For finding the max length
lenght=0
size=len(corpus)
for i in range(size):
    if lenght<len(corpus[i]):
        lenght=len(corpus[i])

print('Number of reviews before removing outliers: ', len(reviews_ints))

## remove any reviews/labels with zero length from the reviews_ints list.
# get indices of any reviews with length 0
non_zero_idx = [ii for ii, review in enumerate(reviews_ints) if len(review) != 0]
print(len(non_zero_idx))

# remove 0-length reviews and their labels
reviews_ints = [reviews_ints[ii] for ii in non_zero_idx]
new_labels = np.array([dataset['Sentiment'][ii] for ii in non_zero_idx])

print('Number of reviews after removing outliers: ', len(reviews_ints))


Zero-length reviews: 32
Maximum review length: 79
Number of reviews before removing outliers:  99989
99957
Number of reviews after removing outliers:  99957


## Padding the Sequence

In [0]:

def pad_features(reviews_ints, seq_length):
    ''' Return features of review_ints, where each review is padded with 0's 
        or truncated to the input seq_length.
    '''
    
    # getting the correct rows x cols shape
    features = np.zeros((len(reviews_ints), seq_length), dtype=int)

    # for each review, I grab that review and 
    for i, row in enumerate(reviews_ints):
        features[i, -len(row):] = np.array(row)[:seq_length]
    
    return features    

seq_length = 150

features = pad_features(reviews_ints, seq_length=seq_length)


##Spliting the dataset

In [15]:
from sklearn.model_selection import train_test_split
xtrain,xtra,ytrain,ytra=train_test_split(features,new_labels,test_size=0.2,random_state=0)    
xval,xtest,yval,ytest=train_test_split(xtra,ytra,test_size=0.5,random_state=0)    

## print out the shapes of your resultant feature data
print("\t\t\tFeature Shapes:")
print("Train set: \t\t{}".format(xtrain.shape), 
      "\nValidation set: \t{}".format(xval.shape),
      "\nTest set: \t\t{}".format(xtest.shape)
     
     )



			Feature Shapes:
Train set: 		(79965, 150) 
Validation set: 	(9996, 150) 
Test set: 		(9996, 150)


In [16]:
ytest.shape



(9996,)

##Dataloading

In [0]:
import torch
from torch.utils.data import TensorDataset, DataLoader

# create Tensor datasets
train_data = TensorDataset(torch.from_numpy(xtrain), torch.from_numpy(ytrain))
valid_data = TensorDataset(torch.from_numpy(xval), torch.from_numpy(yval))
test_data = TensorDataset(torch.from_numpy(xtest), torch.from_numpy(ytest))

# dataloaders
batch_size = 32

# make sure the SHUFFLE your training data
train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size,drop_last=True)
valid_loader = DataLoader(valid_data, shuffle=True, batch_size=batch_size,drop_last=True)
test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size,drop_last=True)



In [18]:
print(len(train_loader))
print(len(valid_loader))
print(len(test_loader))

2498
312
312


##Checking for GPU

In [19]:
# First checking if GPU is available
train_on_gpu=torch.cuda.is_available()

if(train_on_gpu):
    print('Training on GPU.')
else:
    print('No GPU available, training on CPU.')


Training on GPU.


#Creating the architecture of RNN(using class)

In [0]:

import torch.nn as nn

class SentimentRNN(nn.Module):
    """
    The RNN model that will be used to perform Sentiment analysis.
    """

    def __init__(self, vocab_size, output_size, embedding_dim, hidden_dim, n_layers, drop_prob=0.5):
        """
        Initialize the model by setting up the layers.
        """
        super(SentimentRNN, self).__init__()

        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim
        
        # embedding and LSTM layers
        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, n_layers, 
                            dropout=drop_prob, batch_first=True)
        
        # dropout layer
        self.dropout = nn.Dropout(0.3)
        
        # linear and sigmoid layers
        self.fc1 = nn.Linear(hidden_dim, 100)
        self.fc2 = nn.Linear(100, 1)
        
        self.sig = nn.Sigmoid()
        

    def forward(self, x, hidden):
        """
        Perform a forward pass of our model on some input and hidden state.
        """
        batch_size = x.size(0)

        # embeddings and lstm_out
        x = x.long()
        embeds = self.embedding(x)
        lstm_out, hidden = self.lstm(embeds, hidden)
    
        # stack up lstm outputs
        lstm_out = lstm_out.contiguous().view(-1, self.hidden_dim)
        
        # dropout and fully-connected layer
        out = self.dropout(lstm_out)
        out = self.fc1(out)
        out=self.fc2(out)
        # sigmoid function
        sig_out = self.sig(out)
        
        # reshape to be batch_size first
        sig_out = sig_out.view(batch_size, -1)
        sig_out = sig_out[:, -1] # get last batch of labels
        
        # return last sigmoid output and hidden state
        return sig_out, hidden
    
    def init_hidden(self, batch_size):
        ''' Initializes hidden state '''
         # Create two new tensors with sizes n_layers x batch_size x hidden_dim,
         # initialized to zero, for hidden state and cell state of LSTM
        weight = next(self.parameters()).data
        
        if (train_on_gpu):
            hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_().cuda(),
                      weight.new(self.n_layers, batch_size, self.hidden_dim).zero_().cuda())
        else:    
          hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_(),
                      weight.new(self.n_layers, batch_size, self.hidden_dim).zero_())
        
        return hidden

##Model Parameters

In [0]:
# Instantiate the model w/ hyperparams
vocab_size = len(vocab_to_int)+1 # +1 for the 0 padding + our word tokens
output_size = 1
embedding_dim = 300
hidden_dim = 256
n_layers = 2
sd = 1/np.sqrt(embedding_dim)  # Standard deviation to use
weights = np.random.normal(0, scale=sd, size=[vocab_size, embedding_dim])
weights = weights.astype(np.float32)


In [84]:
weights.shape

(85034, 300)

#Using GloVe

In [0]:
from io import open
file = "/content/drive/My Drive/sentiment analysis/glove.6B.300d.txt"

# EXTRACT DESIRED GLOVE WORD VECTORS FROM TEXT FILE
with open(file, encoding="utf-8", mode="r") as textFile:
    for line in textFile:
        # Separate the values from the word
        line = line.split()
        word = line[0]

        # If word is in our vocab, then update the corresponding weights
        id = vocab_to_int.get(word, None)
        if id is not None:
            weights[id] = np.array(line[1:], dtype=np.float32)

##Initializing model

In [107]:
net = SentimentRNN(vocab_size, output_size, embedding_dim, hidden_dim, n_layers)
print('done')

done


##Updating pytorch embeddings

In [0]:
net.embedding.weight.data = torch.Tensor(weights)

##loss and optimization functions

In [109]:

lr=0.001

criterion = nn.BCELoss()
optimizer = torch.optim.Adam(net.parameters(), lr=lr)
print('done')

done


#Training

In [110]:
# training params

epochs = 1# 3 is approx where I noticed the validation loss stop decreasing

counter = 0
print_every = 100
clip=5 # gradient clipping

# move model to GPU, if available
if(train_on_gpu):
    net.cuda()

net.train()
# train for some number of epochs
for e in range(epochs):
    # initialize hidden state
    h = net.init_hidden(batch_size)

    # batch loop
    for inputs, labels in train_loader:
        counter += 1

        if(train_on_gpu):
            inputs, labels = inputs.cuda(), labels.cuda()

        # Creating new variables for the hidden state, otherwise
        # we'd backprop through the entire training history
        h = tuple([each.data for each in h])

        # zero accumulated gradients
        net.zero_grad()

        # get the output from the model
        output, h = net(inputs, h)

        # calculate the loss and perform backprop
        loss = criterion(output.squeeze(), labels.float())
        loss.backward()
        # `clip_grad_norm` helps prevent the exploding gradient problem in RNNs / LSTMs.
        nn.utils.clip_grad_norm_(net.parameters(), clip)
        optimizer.step()

        # loss stats
        if counter % print_every == 0:
            # Get validation loss
            val_h = net.init_hidden(batch_size)
            val_losses = []
            net.eval()
            for inputs, labels in valid_loader:

                # Creating new variables for the hidden state, otherwise
                # we'd backprop through the entire training history
                val_h = tuple([each.data for each in val_h])

                if(train_on_gpu):
                    inputs, labels = inputs.cuda(), labels.cuda()

                output, val_h = net(inputs, val_h)
                val_loss = criterion(output.squeeze(), labels.float())

                val_losses.append(val_loss.item())

            net.train()
            print("Epoch: {}/{}...".format(e+1, epochs),
                  "Step: {}...".format(counter),
                  "Loss: {:.6f}...".format(loss.item()),
                  "Val Loss: {:.6f}".format(np.mean(val_losses)))


Epoch: 1/1... Step: 100... Loss: 0.515607... Val Loss: 0.614206
Epoch: 1/1... Step: 200... Loss: 0.461444... Val Loss: 0.574387
Epoch: 1/1... Step: 300... Loss: 0.452127... Val Loss: 0.559010
Epoch: 1/1... Step: 400... Loss: 0.476866... Val Loss: 0.544970
Epoch: 1/1... Step: 500... Loss: 0.518443... Val Loss: 0.534616
Epoch: 1/1... Step: 600... Loss: 0.642781... Val Loss: 0.531302
Epoch: 1/1... Step: 700... Loss: 0.494281... Val Loss: 0.525092
Epoch: 1/1... Step: 800... Loss: 0.531467... Val Loss: 0.515658
Epoch: 1/1... Step: 900... Loss: 0.555948... Val Loss: 0.516790
Epoch: 1/1... Step: 1000... Loss: 0.517461... Val Loss: 0.525957
Epoch: 1/1... Step: 1100... Loss: 0.400406... Val Loss: 0.519089
Epoch: 1/1... Step: 1200... Loss: 0.485477... Val Loss: 0.510185
Epoch: 1/1... Step: 1300... Loss: 0.412728... Val Loss: 0.504842
Epoch: 1/1... Step: 1400... Loss: 0.490396... Val Loss: 0.504098
Epoch: 1/1... Step: 1500... Loss: 0.507505... Val Loss: 0.510134
Epoch: 1/1... Step: 1600... Loss: 

#Testing

In [111]:
# Get test data loss and accuracy

test_losses = [] # track loss
num_correct = 0

# init hidden state
h = net.init_hidden(batch_size)

net.eval()
# iterate over test data
ypred=[]
count=0

for inputs, labels in test_loader:
    count+=1
    # Creating new variables for the hidden state, otherwise
    # we'd backprop through the entire training history
    h = tuple([each.data for each in h])

    if(train_on_gpu):
        inputs, labels = inputs.cuda(), labels.cuda()
    
    # get predicted outputs
    output, h = net(inputs, h)
    
    # calculate loss
    test_loss = criterion(output.squeeze(), labels.float())
    ##ypred.append()
    test_losses.append(test_loss.item())
    
    # convert output probabilities to predicted class (0 or 1)
    pred = torch.round(output.squeeze())  # rounds to the nearest integer
    #print(len(pred),len(labels))
    ypred.extend(pred)
    
    # compare predictions to true label
    correct_tensor = pred.eq(labels.float().view_as(pred))
    correct = np.squeeze(correct_tensor.numpy()) if not train_on_gpu else np.squeeze(correct_tensor.cpu().numpy())
    num_correct += np.sum(correct)


# -- stats! -- ##
# avg test loss
print("Test loss: {:.3f}".format(np.mean(test_losses)))

# accuracy over all test data
test_acc = num_correct/len(test_loader.dataset)
print("Test accuracy: {:.3f}".format(test_acc))

#print(len(ypred))
ytestt=ytest[:len(ypred)]
#print(len(ypred))
from sklearn.metrics import f1_score
test=np.asarray(ytestt)
ypred=np.asarray(ypred)
ypred=ypred.astype(int)
score=f1_score(ytestt,ypred)
print("F1 score is: {:.3f}".format(score))

from sklearn.metrics import average_precision_score
average_precision = average_precision_score(ytestt,ypred)
print('Average precision-recall score: {:0.3f}'.format(average_precision))
from sklearn.metrics import recall_score
recall_score=recall_score(ytestt, ypred)
print('Average recall score: {:0.3f}'.format(recall_score))


Test loss: 0.508
Test accuracy: 0.743
F1 score is: 0.594
Average precision-recall score: 0.564
Average recall score: 0.625


In [0]:
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score

cnf_matrix = confusion_matrix(ytestt, ypred)



In [113]:
cnf_matrix

array([[1727, 2673],
       [2095, 3489]])